# Historical Data Load  - Drought


The goal of preparing this jupyter is to source information on the Drought in California. Drought is one of the factors that increase forest fires, so this is an important input factor. 

---
**Project Title:** California wildfires

**Modul:** Data Warehouse and Data Lake Systems 1 (FS 2022)

**Autor:** Maren Forrer

**Browser:** Firefox (Version 99)

**Python:** Python 3.9.5

**Einreichungsdatum:** 24.04.2022

---

In [1]:
# import packages
import psycopg2 # pip install psycopg2-binary
import json # already given
import pandas as pd
import numpy as np
import requests
import datetime
from datetime import date
from datetime import datetime, timedelta



## Data Exploring

In [2]:
# load the data
response = requests.get('https://usdmdataservices.unl.edu/api/CountyStatistics/GetDroughtSeverityStatisticsByAreaPercent?aoi=CA&startdate=1/1/2013&enddate=3/28/2022&statisticsType=1')
data = response.json()


In [3]:
# normalize the json -> transform json to a data frame
df_drought = pd.json_normalize(data)
df_drought

MapDate   FIPS          County State    None      D0      D1      D2  \
0      20220322  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
1      20220315  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
2      20220308  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
3      20220301  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
4      20220222  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
...         ...    ...             ...   ...     ...     ...     ...     ...   
27951  20130129  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27952  20130122  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27953  20130115  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27954  20130108  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27955  20130101  06115     Yuba County    CA  100.00    0.00    0.00    0.00   

         D3    D4  ValidStart    ValidEnd StatisticFormatID  
0      0.00  0.00  2022-03-22  2022-03-28                 1  
1      0.00  0.00  2022-03-15  2022-03-21                 1  
2      0.00  0.00  2022-03-08  2022-03-14                 1  
3      0.00  0.00  2022-03-01  2022-03-07                 1  
4      0.00  0.00  2022-02-22  2022-02-28                 1  
...     ...   ...         ...         ...               ...  
27951  0.00  0.00  2013-01-29  2013-02-04                 1  
27952  0.00  0.00  2013-01-22  2013-01-28                 1  
27953  0.00  0.00  2013-01-15  2013-01-21                 1  
27954  0.00  0.00  2013-01-08  2013-01-14                 1  
27955  0.00  0.00  2013-01-01  2013-01-07                 1  

[27956 rows x 13 columns]

In [4]:
df_drought.info

<bound method DataFrame.info of         MapDate   FIPS          County State    None      D0      D1      D2  \
0      20220322  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
1      20220315  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
2      20220308  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
3      20220301  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
4      20220222  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
...         ...    ...             ...   ...     ...     ...     ...     ...   
27951  20130129  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27952  20130122  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27953  20130115  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27954  20130108  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
27955  20130101  06115     Yuba County    CA  100.00    0.00    0.00    0.00   

       

In [5]:
df_drought.describe()

MapDate   FIPS        County  State   None      D0      D1     D2  \
count      27956  27956         27956  27956  27956   27956   27956  27956   
unique       482     58            58      1   1025    1025     952    820   
top     20210608  06001  Butte County     CA   0.00  100.00  100.00   0.00   
freq          58    482           482  27956  19580   19580   15592  12101   

           D3     D4  ValidStart    ValidEnd StatisticFormatID  
count   27956  27956       27956       27956             27956  
unique    680    384         482         482                 1  
top      0.00   0.00  2013-04-02  2021-05-24                 1  
freq    17007  21071          58          58             27956

In [10]:
df_drought.isna().sum().sum()

0

In [11]:
max_value = df_drought['ValidStart'].max()
print(max_value)

2022-03-22


In [12]:
min_value = df_drought['ValidStart'].min()
print(min_value)

2013-01-01


## Load historical Data

In [4]:
# Only Historical data - since the reccring data should get uploaded each month with a DAG (Apache Airflow) 
# a start date have to bet set - since the DAG runs every 30 days - the logic gets adjusted.

#Historical data range up to the date -> Starte and End Date

EndDate = date.today() - timedelta(days=31) 
useEndDate = EndDate.strftime('X%m/X%d/%Y').replace('X0','X').replace('X','')

StartDate = date.today() - timedelta(days=36500) 
useStarteDate = StartDate.strftime('X%m/X%d/%Y').replace('X0','X').replace('X','')


# URL adjustment for the monthly upload
a= "https://usdmdataservices.unl.edu/api/CountyStatistics/GetDroughtSeverityStatisticsByAreaPercent?aoi=CA&startdate="
b= useStarteDate
c= "&enddate="
d= useEndDate
e= "&statisticsType=1"
url = a+b+c+d+e
url

'https://usdmdataservices.unl.edu/api/CountyStatistics/GetDroughtSeverityStatisticsByAreaPercent?aoi=CA&startdate=5/18/1922&enddate=3/23/2022&statisticsType=1'

In [5]:
response = requests.get(url)
data = response.json()

In [6]:
# transform the json to a DataFrame
df_drought_historical = pd.json_normalize(data)

In [7]:
# add a colum with the data of upload
df_drought_historical['dateOfUpload'] = date.today()   # Y-M-D


In [27]:
df_drought_historical #.head(5)

MapDate   FIPS          County State    None      D0      D1      D2  \
0      20220322  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
1      20220315  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
2      20220308  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
3      20220301  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
4      20220222  06001  Alameda County    CA    0.00  100.00  100.00  100.00   
...         ...    ...             ...   ...     ...     ...     ...     ...   
67275  20000201  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
67276  20000125  06115     Yuba County    CA  100.00    0.00    0.00    0.00   
67277  20000118  06115     Yuba County    CA    0.00  100.00    0.00    0.00   
67278  20000111  06115     Yuba County    CA    0.00  100.00    0.00    0.00   
67279  20000104  06115     Yuba County    CA   11.87   88.13    0.00    0.00   

         D3    D4  ValidStart    ValidEnd StatisticFormatID dateOfUpload  
0      0.00  0.00  2022-03-22  2022-03-28                 1   2022-04-23  
1      0.00  0.00  2022-03-15  2022-03-21                 1   2022-04-23  
2      0.00  0.00  2022-03-08  2022-03-14                 1   2022-04-23  
3      0.00  0.00  2022-03-01  2022-03-07                 1   2022-04-23  
4      0.00  0.00  2022-02-22  2022-02-28                 1   2022-04-23  
...     ...   ...         ...         ...               ...          ...  
67275  0.00  0.00  2000-02-01  2000-02-07                 1   2022-04-23  
67276  0.00  0.00  2000-01-25  2000-01-31                 1   2022-04-23  
67277  0.00  0.00  2000-01-18  2000-01-24                 1   2022-04-23  
67278  0.00  0.00  2000-01-11  2000-01-17                 1   2022-04-23  
67279  0.00  0.00  2000-01-04  2000-01-10                 1   2022-04-23  

[67280 rows x 14 columns]

### Creat Postgresql tables and upload the historical data


In [8]:
# Read credentials from json
credentialsFile = open('credentialsForrer.json')
credentials = json.load(credentialsFile)
credentialsFile.close()
credentialsDic = credentials['credentialsForrer'][0]


In [9]:
# Connect with the RDS - via credentials from json
connectionRequest = "host=" + credentialsDic['rds_host'] + "  dbname=" + credentialsDic['db_name'] + " user=" + credentialsDic['name'] + " password=" + credentialsDic['password']
try: 
    conn = psycopg2.connect(connectionRequest)
except psycopg2.Error as e: 
    print("Error: Could not make connection to the Postgres database")
    print(e)
 
   

In [10]:
try: 
    cur = conn.cursor()
except psycopg2.Error as e: 
    print("Error: Could not get curser to the Database")
    print(e)
    # Auto commit is very important
conn.set_session(autocommit=True)

In [20]:
# SQL Query to count how many rows the table has. - Check if table is empthy before the one time historical upload.  
cur.execute("select count(*) from Drought_history;")
print(cur.fetchall())

[(67280,)]


In [64]:
# Only needed if the table is not empty
#cur.execute("TRUNCATE TABLE Drought")

In [11]:
# creat the first table (total)
# first upload : it is important that the list is empthy:


cur.execute("CREATE TABLE IF NOT EXISTS Drought_History ( MapDate varchar(10) ,FIPS varchar(10), County varchar(255) ,State varchar(10), None FLOAT ,D0 FLOAT ,D1 FLOAT ,D2 FLOAT ,D3 FLOAT ,D4 FLOAT,ValidStart DATE,ValidEnd DATE ,StatisticFormatID INTEGER, dateOfUpload DATE)")
            

In [ ]:
# upload the entries from the firt table (total)

# rename the DF - in this case the below function must not be changed
data = df_drought_historical

# Columns Definition 
cols = ",".join([str(i) for i in data.columns.tolist()])

#  uploaed each value to Postgree SQL 
for i,row in data.iterrows():
    sql = "INSERT INTO Drought_History (" +cols + ") VALUES (" + "%s,"*(len(row)-1) + "%s)"
    cur.execute(sql, tuple(row))

    # save all changes
    conn.commit()



In [74]:
# Test Upload 

len(df_drought_historical)

# Vergleich der Anzahl Zeilen zuerste aus Jupyter dann ein Foto vom Terminal (MariaDB)
# Jupyter:
df_drought_historical.shape

(67280, 14)

In [75]:
cur.execute("select count(*) from Drought_History;")
print(cur.fetchall())

[(67280,)]


In [73]:
# Show the rows from RDS
try: 
    cur.execute("SELECT * FROM Drought_History;")
except psycopg2.Error as e: 
    print("Error: select *")
    print (e)

row = cur.fetchone()
while row:
   print(row)
   row = cur.fetchone()

('20220322', '06001', 'Alameda County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2022, 3, 22), datetime.date(2022, 3, 28), 1, datetime.date(2022, 4, 21))
('20220315', '06001', 'Alameda County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2022, 3, 15), datetime.date(2022, 3, 21), 1, datetime.date(2022, 4, 21))
('20220308', '06001', 'Alameda County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2022, 3, 8), datetime.date(2022, 3, 14), 1, datetime.date(2022, 4, 21))
('20220301', '06001', 'Alameda County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2022, 3, 1), datetime.date(2022, 3, 7), 1, datetime.date(2022, 4, 21))
('20220222', '06001', 'Alameda County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2022, 2, 22), datetime.date(2022, 2, 28), 1, datetime.date(2022, 4, 21))
('20220215', '06001', 'Alameda County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2022, 2, 15), datetime.date(2022, 2, 21), 1, datetime.date(202

('20190514', '06003', 'Alpine County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2019, 5, 14), datetime.date(2019, 5, 20), 1, datetime.date(2022, 4, 21))
('20190507', '06003', 'Alpine County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2019, 5, 7), datetime.date(2019, 5, 13), 1, datetime.date(2022, 4, 21))
('20190430', '06003', 'Alpine County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2019, 4, 30), datetime.date(2019, 5, 6), 1, datetime.date(2022, 4, 21))
('20190423', '06003', 'Alpine County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2019, 4, 23), datetime.date(2019, 4, 29), 1, datetime.date(2022, 4, 21))
('20190416', '06003', 'Alpine County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2019, 4, 16), datetime.date(2019, 4, 22), 1, datetime.date(2022, 4, 21))
('20190409', '06003', 'Alpine County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2019, 4, 9), datetime.date(2019, 4, 15), 1, datetime.date(2022, 4, 21))
('20190402', '06003

('20031028', '06003', 'Alpine County', 'CA', 0.0, 100.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 10, 28), datetime.date(2003, 11, 3), 1, datetime.date(2022, 4, 21))
('20031021', '06003', 'Alpine County', 'CA', 62.63, 37.37, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 10, 21), datetime.date(2003, 10, 27), 1, datetime.date(2022, 4, 21))
('20031014', '06003', 'Alpine County', 'CA', 15.58, 84.42, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 10, 14), datetime.date(2003, 10, 20), 1, datetime.date(2022, 4, 21))
('20031007', '06003', 'Alpine County', 'CA', 53.27, 46.73, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 10, 7), datetime.date(2003, 10, 13), 1, datetime.date(2022, 4, 21))
('20030930', '06003', 'Alpine County', 'CA', 47.83, 52.17, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 9, 30), datetime.date(2003, 10, 6), 1, datetime.date(2022, 4, 21))
('20030923', '06003', 'Alpine County', 'CA', 48.49, 51.51, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 9, 23), datetime.date(2003, 9, 29), 1, datetime.date(2022, 4, 21))


('20031202', '06005', 'Amador County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 12, 2), datetime.date(2003, 12, 8), 1, datetime.date(2022, 4, 21))
('20031125', '06005', 'Amador County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 11, 25), datetime.date(2003, 12, 1), 1, datetime.date(2022, 4, 21))
('20031118', '06005', 'Amador County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 11, 18), datetime.date(2003, 11, 24), 1, datetime.date(2022, 4, 21))
('20031111', '06005', 'Amador County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 11, 11), datetime.date(2003, 11, 17), 1, datetime.date(2022, 4, 21))
('20031104', '06005', 'Amador County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 11, 4), datetime.date(2003, 11, 10), 1, datetime.date(2022, 4, 21))
('20031028', '06005', 'Amador County', 'CA', 0.0, 100.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2003, 10, 28), datetime.date(2003, 11, 3), 1, datetime.date(2022, 4, 21))
('2003102

('20020709', '06007', 'Butte County', 'CA', 0.0, 100.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2002, 7, 9), datetime.date(2002, 7, 15), 1, datetime.date(2022, 4, 21))
('20020702', '06007', 'Butte County', 'CA', 0.0, 100.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2002, 7, 2), datetime.date(2002, 7, 8), 1, datetime.date(2022, 4, 21))
('20020625', '06007', 'Butte County', 'CA', 0.0, 100.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2002, 6, 25), datetime.date(2002, 7, 1), 1, datetime.date(2022, 4, 21))
('20020618', '06007', 'Butte County', 'CA', 5.38, 94.62, 0.0, 0.0, 0.0, 0.0, datetime.date(2002, 6, 18), datetime.date(2002, 6, 24), 1, datetime.date(2022, 4, 21))
('20020611', '06007', 'Butte County', 'CA', 5.58, 94.42, 0.0, 0.0, 0.0, 0.0, datetime.date(2002, 6, 11), datetime.date(2002, 6, 17), 1, datetime.date(2022, 4, 21))
('20020604', '06007', 'Butte County', 'CA', 5.33, 94.67, 0.0, 0.0, 0.0, 0.0, datetime.date(2002, 6, 4), datetime.date(2002, 6, 10), 1, datetime.date(2022, 4, 21))
('20020528', '06007', 'B

...

('20081118', '06103', 'Tehama County', 'CA', 0.0, 100.0, 100.0, 82.8, 0.0, 0.0, datetime.date(2008, 11, 18), datetime.date(2008, 11, 24), 1, datetime.date(2022, 4, 21))
('20081111', '06103', 'Tehama County', 'CA', 0.0, 100.0, 100.0, 82.8, 0.0, 0.0, datetime.date(2008, 11, 11), datetime.date(2008, 11, 17), 1, datetime.date(2022, 4, 21))
('20081104', '06103', 'Tehama County', 'CA', 0.0, 100.0, 100.0, 91.38, 0.0, 0.0, datetime.date(2008, 11, 4), datetime.date(2008, 11, 10), 1, datetime.date(2022, 4, 21))
('20081028', '06103', 'Tehama County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2008, 10, 28), datetime.date(2008, 11, 3), 1, datetime.date(2022, 4, 21))
('20081021', '06103', 'Tehama County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2008, 10, 21), datetime.date(2008, 10, 27), 1, datetime.date(2022, 4, 21))
('20081014', '06103', 'Tehama County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2008, 10, 14), datetime.date(2008, 10, 20), 1, datetime.dat

('20101228', '06105', 'Trinity County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2010, 12, 28), datetime.date(2011, 1, 3), 1, datetime.date(2022, 4, 21))
('20101221', '06105', 'Trinity County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2010, 12, 21), datetime.date(2010, 12, 27), 1, datetime.date(2022, 4, 21))
('20101214', '06105', 'Trinity County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2010, 12, 14), datetime.date(2010, 12, 20), 1, datetime.date(2022, 4, 21))
('20101207', '06105', 'Trinity County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2010, 12, 7), datetime.date(2010, 12, 13), 1, datetime.date(2022, 4, 21))
('20101130', '06105', 'Trinity County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2010, 11, 30), datetime.date(2010, 12, 6), 1, datetime.date(2022, 4, 21))
('20101123', '06105', 'Trinity County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2010, 11, 23), datetime.date(2010, 11, 29), 1, datetime.date(2022, 4, 21))
('

('20071211', '06107', 'Tulare County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2007, 12, 11), datetime.date(2007, 12, 17), 1, datetime.date(2022, 4, 21))
('20071204', '06107', 'Tulare County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2007, 12, 4), datetime.date(2007, 12, 10), 1, datetime.date(2022, 4, 21))
('20071127', '06107', 'Tulare County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2007, 11, 27), datetime.date(2007, 12, 3), 1, datetime.date(2022, 4, 21))
('20071120', '06107', 'Tulare County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2007, 11, 20), datetime.date(2007, 11, 26), 1, datetime.date(2022, 4, 21))
('20071113', '06107', 'Tulare County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2007, 11, 13), datetime.date(2007, 11, 19), 1, datetime.date(2022, 4, 21))
('20071106', '06107', 'Tulare County', 'CA', 0.0, 100.0, 100.0, 100.0, 0.0, 0.0, datetime.date(2007, 11, 6), datetime.date(2007, 11, 12), 1, datetime.da

('20051115', '06109', 'Tuolumne County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2005, 11, 15), datetime.date(2005, 11, 21), 1, datetime.date(2022, 4, 21))
('20051108', '06109', 'Tuolumne County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2005, 11, 8), datetime.date(2005, 11, 14), 1, datetime.date(2022, 4, 21))
('20051101', '06109', 'Tuolumne County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2005, 11, 1), datetime.date(2005, 11, 7), 1, datetime.date(2022, 4, 21))
('20051025', '06109', 'Tuolumne County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2005, 10, 25), datetime.date(2005, 10, 31), 1, datetime.date(2022, 4, 21))
('20051018', '06109', 'Tuolumne County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2005, 10, 18), datetime.date(2005, 10, 24), 1, datetime.date(2022, 4, 21))
('20051011', '06109', 'Tuolumne County', 'CA', 100.0, 0.0, 0.0, 0.0, 0.0, 0.0, datetime.date(2005, 10, 11), datetime.date(2005, 10, 17), 1, datetime.date(2022, 4, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [30]:
# Close the connection
cur.close()
conn.close()